In [ ]:
!pip install tensorflow-hub

In [ ]:
import os
import cv2
import numpy as np
import pandas as pd
import tensorflow as tf
import tensorflow_hub as hub  # Note the separate import

In [ ]:
import csv

In [ ]:
# from tensorflow.keras.utils import plot_model

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# Define the path to your dataset
MOUNT_PATH='/content/drive/MyDrive/FYP_Research_Work/Cosine Transformer/dataset'
dataset_path = f"{MOUNT_PATH}/classes"
# MOUNT_PATH='/content/drive/MyDrive/FYP_Research_Work/dataset'
# dataset_path = f"{MOUNT_PATH}/CustomYogaPosesDataset"

In [ ]:
# Define your target directory to save the processed images
output_directory = f"{dataset_path}/Keypoints"

# Create the output directory if it doesn't exist
os.makedirs(output_directory, exist_ok=True)

In [ ]:
# Resize images to a consistent size (e.g., 224x224) and normalize pixel values
target_size = (448,448)

In [ ]:
model_name = "movenet_thunder" #@param ["movenet_lightning", "movenet_thunder", "movenet_lightning_f16.tflite", "movenet_thunder_f16.tflite", "movenet_lightning_int8.tflite", "movenet_thunder_int8.tflite"]

if "tflite" in model_name:
  if "movenet_lightning_f16" in model_name:
    !wget -q -O model.tflite https://tfhub.dev/google/lite-model/movenet/singlepose/lightning/tflite/float16/4?lite-format=tflite
    input_size = 192
  elif "movenet_thunder_f16" in model_name:
    !wget -q -O model.tflite https://tfhub.dev/google/lite-model/movenet/singlepose/thunder/tflite/float16/4?lite-format=tflite
    input_size = 256
  elif "movenet_lightning_int8" in model_name:
    !wget -q -O model.tflite https://tfhub.dev/google/lite-model/movenet/singlepose/lightning/tflite/int8/4?lite-format=tflite
    input_size = 192
  elif "movenet_thunder_int8" in model_name:
    !wget -q -O model.tflite https://tfhub.dev/google/lite-model/movenet/singlepose/thunder/tflite/int8/4?lite-format=tflite
    input_size = 256
  else:
    raise ValueError("Unsupported model name: %s" % model_name)

  # Initialize the TFLite interpreter
  interpreter = tf.lite.Interpreter(model_path="model.tflite")
  interpreter.allocate_tensors()

  def movenet(input_image):
    """Runs detection on an input image.

    Args:
      input_image: A [1, height, width, 3] tensor represents the input image
        pixels. Note that the height/width should already be resized and match the
        expected input resolution of the model before passing into this function.

    Returns:
      A [1, 1, 17, 3] float numpy array representing the predicted keypoint
      coordinates and scores.
    """
    # TF Lite format expects tensor type of uint8.
    input_image = tf.cast(input_image, dtype=tf.uint8)
    input_details = interpreter.get_input_details()
    output_details = interpreter.get_output_details()
    interpreter.set_tensor(input_details[0]['index'], input_image.numpy())
    # Invoke inference.
    interpreter.invoke()
    # Get the model prediction.
    keypoints_with_scores = interpreter.get_tensor(output_details[0]['index'])
    return keypoints_with_scores

else:
  if "movenet_lightning" in model_name:
    module = hub.load("https://tfhub.dev/google/movenet/singlepose/lightning/4")
    input_size = 192
  elif "movenet_thunder" in model_name:
    module = hub.load("https://tfhub.dev/google/movenet/singlepose/thunder/4")
    input_size = 256
  else:
    raise ValueError("Unsupported model name: %s" % model_name)

  def movenet(input_image):
    """Runs detection on an input image.

    Args:
      input_image: A [1, height, width, 3] tensor represents the input image
        pixels. Note that the height/width should already be resized and match the
        expected input resolution of the model before passing into this function.

    Returns:
      A [1, 1, 17, 3] float numpy array representing the predicted keypoint
      coordinates and scores.
    """
    model = module.signatures['serving_default']

    # Print model summary
    print(model)

    # SavedModel format expects tensor type of int32.
    input_image = tf.cast(input_image, dtype=tf.int32)
    # Run model inference.
    outputs = model(input_image)
    # Output is a [1, 1, 17, 3] tensor.
    keypoints_with_scores = outputs['output_0'].numpy()
    return keypoints_with_scores

# Model Testing

In [ ]:
module = hub.load("https://tfhub.dev/google/movenet/singlepose/lightning/4")
model = module.signatures['serving_default']

In [ ]:
# Check the type of the loaded model
print(type(module))

<class 'tensorflow.python.saved_model.load.Loader._recreate_base_user_object.<locals>._UserObject'>


In [ ]:
# Print information about the model
print(module.signatures.keys())  # Print available signatures of the model

KeysView(_SignatureMap({'serving_default': <ConcreteFunction (*, input: TensorSpec(shape=(1, 192, 192, 3), dtype=tf.int32, name='input')) -> Dict[['output_0', TensorSpec(shape=(1, 1, 17, 3), dtype=tf.float32, name='output_0')]] at 0x781CBFBDF250>}))


In [ ]:
# Inspect the model's input and output details
print(module.signatures['serving_default'].inputs)
print(module.signatures['serving_default'].outputs)

[<tf.Tensor 'input:0' shape=(1, 192, 192, 3) dtype=int32>, <tf.Tensor 'unknown:0' shape=() dtype=resource>, <tf.Tensor 'unknown_0:0' shape=() dtype=resource>, <tf.Tensor 'unknown_1:0' shape=() dtype=resource>, <tf.Tensor 'unknown_2:0' shape=() dtype=resource>, <tf.Tensor 'unknown_3:0' shape=() dtype=resource>, <tf.Tensor 'unknown_4:0' shape=() dtype=resource>, <tf.Tensor 'unknown_5:0' shape=() dtype=resource>, <tf.Tensor 'unknown_6:0' shape=() dtype=resource>, <tf.Tensor 'unknown_7:0' shape=() dtype=resource>, <tf.Tensor 'unknown_8:0' shape=() dtype=resource>, <tf.Tensor 'unknown_9:0' shape=() dtype=resource>, <tf.Tensor 'unknown_10:0' shape=() dtype=resource>, <tf.Tensor 'unknown_11:0' shape=() dtype=resource>, <tf.Tensor 'unknown_12:0' shape=() dtype=resource>, <tf.Tensor 'unknown_13:0' shape=() dtype=resource>, <tf.Tensor 'unknown_14:0' shape=() dtype=resource>, <tf.Tensor 'unknown_15:0' shape=() dtype=resource>, <tf.Tensor 'unknown_16:0' shape=() dtype=resource>, <tf.Tensor 'unknow

# Back to Normal

In [ ]:
# import pydot

# dot_img = pydot.Dot()
# for i, layer in enumerate(model.layers):
#     dot_img.add_node(pydot.Node(str(i), label=layer.name))
#     for node in layer.outbound_nodes:
#         dot_img.add_edge(pydot.Edge(str(i), str(node.index)))
# dot_img.write_png('model_architecture.png')
# #

In [ ]:
# keras_model = tf.keras.models.Model.from_config(model.get_config())
# #

In [ ]:

# plot_model(model, to_file="model_plot.png", show_shapes=True, show_layer_names=True)
# print(model.summary())

In [ ]:
keypoints = []
labels = []
classes = []
image_paths = []
input_size = 256

In [ ]:
# Load the input image.
image_path = '/content/drive/MyDrive/FYP_Research_Work/dataset/CustomYogaPoses/Virabhadrasana Two/File1.png'
image = tf.io.read_file(image_path)
image = tf.image.decode_jpeg(image)

In [ ]:
# Resize and pad the image to keep the aspect ratio and fit the expected size.
input_image = tf.expand_dims(image, axis=0)
input_image = tf.image.resize_with_pad(input_image, input_size, input_size)

# Run model inference.
keypoints_with_scores = movenet(input_image)

# Visualize the predictions with image.
# display_image = tf.expand_dims(image, axis=0)
# display_image = tf.cast(tf.image.resize_with_pad(
#     display_image, 1280, 1280), dtype=tf.int32)

keypoints_with_scores[0][0]

ConcreteFunction Input Parameters:
  input (KEYWORD_ONLY): TensorSpec(shape=(1, 256, 256, 3), dtype=tf.int32, name='input')
Output Type:
  Dict[['output_0', TensorSpec(shape=(1, 1, 17, 3), dtype=tf.float32, name='output_0')]]
Captures:
  132064957671632: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065000477392: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065000483552: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065000477568: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065000481264: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064957671456: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065000481440: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065000482320: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065000479856: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065000484256: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064957668464: TensorSpec(shape=(), dtype=tf.resource, name=

array([[0.20557837, 0.5802898 , 0.79700595],
       [0.18585686, 0.57167315, 0.8450375 ],
       [0.18427923, 0.5647576 , 0.7953337 ],
       [0.18574312, 0.51818925, 0.77807057],
       [0.18379101, 0.5056987 , 0.7775369 ],
       [0.28467909, 0.58916646, 0.77519155],
       [0.27456453, 0.40522856, 0.79582447],
       [0.26875657, 0.7333284 , 0.96544886],
       [0.262708  , 0.23791836, 0.9030813 ],
       [0.26384693, 0.87366647, 0.7639626 ],
       [0.24833691, 0.11012823, 0.7113187 ],
       [0.578905  , 0.5209022 , 0.91802573],
       [0.5801016 , 0.41241947, 0.8219147 ],
       [0.63484687, 0.7384883 , 0.8735209 ],
       [0.73946273, 0.24101657, 0.83511823],
       [0.86633724, 0.73015547, 0.8983233 ],
       [0.8712214 , 0.06300681, 0.7649604 ]], dtype=float32)

In [ ]:
# Iterate through each subfolder (pose) in the dataset
for label, pose in enumerate(sorted(os.listdir(dataset_path))):
    pose_path = os.path.join(dataset_path, pose)

    # Check if the item in the folder is indeed a subfolder (pose)
    if os.path.isdir(pose_path):
        for image_filename in os.listdir(pose_path):
            # Check if the file is indeed an image file
            if image_filename.lower().endswith(('.jpg', '.jpeg', '.png', '.gif')):
                # Append the image path and corresponding label
                image_path = os.path.join(pose_path, image_filename)
                image = tf.io.read_file(image_path)
                image = tf.image.decode_jpeg(image)
                if image is not None:
                  # Resize and pad the image to keep the aspect ratio and fit the expected size.
                  input_image = tf.expand_dims(image, axis=0)
                  input_image = tf.image.resize_with_pad(input_image, input_size, input_size)


                try:
                    # Run model inference.
                    keypoints_with_scores = movenet(input_image)
                    labels.append(label)
                    classes.append(pose)
                    num_instances, _, _, _ = keypoints_with_scores.shape
                    # for idx in range(num_instances):
                    #   kpts_x = keypoints_with_scores[0, idx, :, 1]
                    #   kpts_y = keypoints_with_scores[0, idx, :, 0]
                    #   kpts_scores = keypoints_with_scores[0, idx, :, 2]
                    keypoints.append(keypoints_with_scores[0][0])
                    image_paths.append(image_path)
                except Exception as e:
                    print(f"Error creating image from file: {image_path}. Exception: {e}")


Streaming output truncated to the last 5000 lines.
  132064939767616: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064846455808: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064846455456: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064846455632: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064846455984: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064939767440: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064846455280: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064846455104: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064846454752: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064846454928: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064939767264: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064846454400: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064846454224: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064846454576: TensorSpec(shape=(),

In [ ]:
keypoints

[array([[0.6441565 , 0.4670998 , 0.74062914],
        [0.65457326, 0.44342688, 0.60968435],
        [0.6527129 , 0.4425789 , 0.61767256],
        [0.6248396 , 0.40990397, 0.69232136],
        [0.62165016, 0.40593413, 0.6220944 ],
        [0.55732405, 0.42880335, 0.7678733 ],
        [0.548376  , 0.4307836 , 0.71603817],
        [0.67565304, 0.3407123 , 0.87162846],
        [0.6482144 , 0.3404241 , 0.71263146],
        [0.7510547 , 0.22129714, 0.79935944],
        [0.713113  , 0.22960192, 0.82714826],
        [0.31796327, 0.6591909 , 0.8140527 ],
        [0.31569543, 0.6526918 , 0.5581159 ],
        [0.5300152 , 0.7934507 , 0.83366513],
        [0.5348201 , 0.78051114, 0.7602109 ],
        [0.7162476 , 0.9445977 , 0.84313124],
        [0.706967  , 0.9018351 , 0.678858  ]], dtype=float32),
 array([[0.5874929 , 0.5530081 , 0.36677733],
        [0.5912886 , 0.57880914, 0.4875698 ],
        [0.5979637 , 0.5423819 , 0.6476953 ],
        [0.5441783 , 0.61291885, 0.6553475 ],
        [0.545959

In [ ]:
class_keypoints = {}

# Iterate through each subfolder (pose) in the dataset
for label, pose in enumerate(sorted(os.listdir(dataset_path))):
    pose_path = os.path.join(dataset_path, pose)

    # Check if the item in the folder is indeed a subfolder (pose)
    if os.path.isdir(pose_path):
        for image_filename in os.listdir(pose_path):
            # Check if the file is indeed an image file
            if image_filename.lower().endswith(('.jpg', '.jpeg', '.png', '.gif')):
                # Append the image path and corresponding label
                image_path = os.path.join(pose_path, image_filename)
                image = tf.io.read_file(image_path)
                image = tf.image.decode_jpeg(image)
                if image is not None:
                  # Resize and pad the image to keep the aspect ratio and fit the expected size.
                  input_image = tf.expand_dims(image, axis=0)
                  input_image = tf.image.resize_with_pad(input_image, input_size, input_size)


                try:
                    # Run model inference.
                    keypoints_with_scores = movenet(input_image)
                    print("keypoints_with_scores: ", keypoints_with_scores[0][0])
                    labels.append(label)
                    classes.append(pose)
                    num_instances, _, _, _ = keypoints_with_scores.shape
                    for idx in range(num_instances):
                      kpts_x = keypoints_with_scores[0, idx, :, 1]
                      kpts_y = keypoints_with_scores[0, idx, :, 0]
                      kpts_scores = keypoints_with_scores[0, idx, :, 2]
                    keypoints.append(keypoints_with_scores[0][0])
                    print("keypoints: ", keypoints)
                    image_paths.append(image_path)
                    # Check if the class exists as a key in the dictionary
                    if pose in class_keypoints:
                        # If it exists, append the keypoints to the existing list
                        class_keypoints[pose].append(keypoints_with_scores[0][0])
                    else:
                        # If it doesn't exist, create a key with an empty list and append the keypoints
                        class_keypoints[pose] = []
                        class_keypoints[pose].append(keypoints_with_scores[0][0])

                except Exception as e:
                    print(f"Error creating image from file: {image_path}. Exception: {e}")


Streaming output truncated to the last 5000 lines.
  132064939763216: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065228812736: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065228812560: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065228812912: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065228812384: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064939762864: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065228811856: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065228811680: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065228812208: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065228812032: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132064939762512: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065228811504: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065228811328: TensorSpec(shape=(), dtype=tf.resource, name=None)
  132065228811152: TensorSpec(shape=(),

In [ ]:
class_keypoints

{}

In [ ]:
class_keypoints = {}
# Iterate through each subfolder (pose) in the dataset
for label, pose in enumerate(sorted(os.listdir(dataset_path))):
    pose_path = os.path.join(dataset_path, pose)
    print("pose: ", pose)

    # Check if the item in the folder is indeed a subfolder (pose)
    if os.path.isdir(pose_path):
        for image_filename in os.listdir(pose_path):
            # Check if the file is indeed an image file
            if image_filename.lower().endswith(('.jpg', '.jpeg', '.png', '.gif')):
                # Append the image path and corresponding label
                image_path = os.path.join(pose_path, image_filename)
                image = tf.io.read_file(image_path)
                image = tf.image.decode_jpeg(image)
                if image is not None:
                  # Resize and pad the image to keep the aspect ratio and fit the expected size.
                  input_image = tf.expand_dims(image, axis=0)
                  input_image = tf.image.resize_with_pad(input_image, input_size, input_size)


                try:
                    # Run model inference.
                    keypoints_with_scores = movenet(input_image)
                    labels.append(label)
                    classes.append(pose)
                    num_instances, _, _, _ = keypoints_with_scores.shape
                    # for idx in range(num_instances):
                    #   kpts_x = keypoints_with_scores[0, idx, :, 1]
                    #   kpts_y = keypoints_with_scores[0, idx, :, 0]
                    #   kpts_scores = keypoints_with_scores[0, idx, :, 2]
                    keypoints.append(keypoints_with_scores[0][0])
                    image_paths.append(image_path)
                    # Check if the class exists as a key in the dictionary

                    # print("class_keypoints: ", class_keypoints)
                    if pose in class_keypoints:
                        # If it exists, append the keypoints to the existing list
                        print("inside the class_keypoints")
                        class_keypoints[pose].append(keypoints_with_scores[0][0])
                    else:
                        # If it doesn't exist, create a key with an empty list and append the keypoints
                        class_keypoints[pose] = []
                        class_keypoints[pose].append(keypoints_with_scores[0][0])
                except Exception as e:
                    print(f"Error creating image from file: {image_path}. Exception: {e}")


# # Iterate through each subfolder (pose) in the dataset
# for label, pose in enumerate(sorted(os.listdir(dataset_path))):
#     pose_path = os.path.join(dataset_path, pose)

#     # Check if the item in the folder is indeed a subfolder (pose)
#     if os.path.isdir(pose_path):
#         for image_filename in os.listdir(pose_path):
#             # Check if the file is indeed an image file
#             if image_filename.lower().endswith(('.jpg', '.jpeg', '.png', '.gif')):
#                 # Append the image path and corresponding label
#                 image_path = os.path.join(pose_path, image_filename)
#                 image = tf.io.read_file(image_path)
#                 image = tf.image.decode_jpeg(image)
#                 if image is not None:
#                   # Resize and pad the image to keep the aspect ratio and fit the expected size.
#                   input_image = tf.expand_dims(image, axis=0)
#                   input_image = tf.image.resize_with_pad(input_image, input_size, input_size)


#                 try:
#                     # Run model inference.
#                     keypoints_with_scores = movenet(input_image)
#                     labels.append(label)
#                     classes.append(pose)
#                     num_instances, _, _, _ = keypoints_with_scores.shape
#                     for idx in range(num_instances):
#                       kpts_x = keypoints_with_scores[0, idx, :, 1]
#                       kpts_y = keypoints_with_scores[0, idx, :, 0]
#                       kpts_scores = keypoints_with_scores[0, idx, :, 2]
#                     keypoints.append(keypoints_with_scores[0][0])
#                     image_paths.append(image_path)
#                     # Check if the class exists as a key in the dictionary
#                     if pose in class_keypoints:
#                         # If it exists, append the keypoints to the existing list
#                         class_keypoints[pose].append(keypoints_with_scores[0][0])
#                     else:
#                         # If it doesn't exist, create a key with an empty list and append the keypoints
#                         class_keypoints[pose] = []
#                         class_keypoints[pose].append(keypoints_with_scores[0][0])

#                 except Exception as e:
#                     print(f"Error creating image from file: {image_path}. Exception: {e}")

Streaming output truncated to the last 5000 lines.
  137150521366784: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150521237648: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150521237296: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150521236416: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150521236768: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150521366432: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150521240640: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150522192144: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150521242576: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150521360800: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150521366080: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150521532736: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150521532384: TensorSpec(shape=(), dtype=tf.resource, name=None)
  137150522190384: TensorSpec(shape=(),

In [ ]:
class_keypoints

{'adho mukha svanasana': [array([[0.6441565 , 0.4670998 , 0.74062914],
         [0.65457326, 0.44342688, 0.60968435],
         [0.6527129 , 0.4425789 , 0.61767256],
         [0.6248396 , 0.40990397, 0.69232136],
         [0.62165016, 0.40593413, 0.6220944 ],
         [0.55732405, 0.42880335, 0.7678733 ],
         [0.548376  , 0.4307836 , 0.71603817],
         [0.67565304, 0.3407123 , 0.87162846],
         [0.6482144 , 0.3404241 , 0.71263146],
         [0.7510547 , 0.22129714, 0.79935944],
         [0.713113  , 0.22960192, 0.82714826],
         [0.31796327, 0.6591909 , 0.8140527 ],
         [0.31569543, 0.6526918 , 0.5581159 ],
         [0.5300152 , 0.7934507 , 0.83366513],
         [0.5348201 , 0.78051114, 0.7602109 ],
         [0.7162476 , 0.9445977 , 0.84313124],
         [0.706967  , 0.9018351 , 0.678858  ]], dtype=float32),
  array([[0.5874929 , 0.5530081 , 0.36677733],
         [0.5912886 , 0.57880914, 0.4875698 ],
         [0.5979637 , 0.5423819 , 0.6476953 ],
         [0.5441783

In [ ]:
for class_name in class_keypoints.keys():
  # Create a CSV file and write the header
  csv_file_path = f"{MOUNT_PATH}/classes/Keypoints/{class_name}_keypoint_dataset.csv"  # Replace with the desired path for the CSV file
  with open(csv_file_path, mode='w', newline='') as csv_file:
      csv_writer = csv.writer(csv_file)
      csv_writer.writerow(['Keypoints', 'Class'])

      # Write each row (image path and label) to the CSV file
      for keypoints in class_keypoints[class_name]:
          csv_writer.writerow([keypoints])

In [ ]:
keypoints

[array([[0.6441565 , 0.4670998 , 0.74062914],
        [0.65457326, 0.44342688, 0.60968435],
        [0.6527129 , 0.4425789 , 0.61767256],
        [0.6248396 , 0.40990397, 0.69232136],
        [0.62165016, 0.40593413, 0.6220944 ],
        [0.55732405, 0.42880335, 0.7678733 ],
        [0.548376  , 0.4307836 , 0.71603817],
        [0.67565304, 0.3407123 , 0.87162846],
        [0.6482144 , 0.3404241 , 0.71263146],
        [0.7510547 , 0.22129714, 0.79935944],
        [0.713113  , 0.22960192, 0.82714826],
        [0.31796327, 0.6591909 , 0.8140527 ],
        [0.31569543, 0.6526918 , 0.5581159 ],
        [0.5300152 , 0.7934507 , 0.83366513],
        [0.5348201 , 0.78051114, 0.7602109 ],
        [0.7162476 , 0.9445977 , 0.84313124],
        [0.706967  , 0.9018351 , 0.678858  ]], dtype=float32),
 array([[0.5874929 , 0.5530081 , 0.36677733],
        [0.5912886 , 0.57880914, 0.4875698 ],
        [0.5979637 , 0.5423819 , 0.6476953 ],
        [0.5441783 , 0.61291885, 0.6553475 ],
        [0.545959

In [ ]:
# Create a CSV file and write the header
csv_file_path = f"{MOUNT_PATH}/classes/keypoint_dataset.csv"  # Replace with the desired path for the CSV file
with open(csv_file_path, mode='w', newline='') as csv_file:
    csv_writer = csv.writer(csv_file)
    csv_writer.writerow(['Keypoints', 'Class'])

    # Write each row (image path and label) to the CSV file
    for keypoints, class_ in zip(keypoints, classes):
        csv_writer.writerow([keypoints, class_])

In [ ]:
feature_1 = []
feature_2 = []
feature_3 = []
feature_4 = []
feature_5 = []
feature_6 = []
feature_7 = []
feature_8 = []
feature_9 = []
feature_10 = []
feature_11 = []
feature_12 = []
feature_13 = []
feature_14 = []
feature_15 = []
feature_16 = []
feature_17 = []

In [ ]:
# Initialize keypoints_dict with empty lists for all keys
keypoints_dict = {f'feature_{i}': [] for i in range(1, 18)}
print(keypoints_dict)

{'feature_1': [], 'feature_2': [], 'feature_3': [], 'feature_4': [], 'feature_5': [], 'feature_6': [], 'feature_7': [], 'feature_8': [], 'feature_9': [], 'feature_10': [], 'feature_11': [], 'feature_12': [], 'feature_13': [], 'feature_14': [], 'feature_15': [], 'feature_16': [], 'feature_17': []}


In [ ]:
# Read the annotations CSV file
dataset_file = "keypoint_dataset_temp.csv"
dataset_file_path = os.path.join(dataset_path, dataset_file)
dataset_df = pd.read_csv(dataset_file)

In [ ]:
dataset_df

Keypoints                 Class
0     0.6441565  0.4670998  0.74062914\n 0.65457326 ...  adho mukha svanasana
1     0.5874929  0.5530081  0.36677733\n 0.5912886  ...  adho mukha svanasana
2     0.7245303  0.50567865 0.37279207\n 0.7374404  ...  adho mukha svanasana
3     0.65779746 0.38198677 0.807082  \n 0.6542191  ...  adho mukha svanasana
4     0.5957581  0.64245814 0.63050437\n 0.59791446 ...  adho mukha svanasana
...                                                 ...                   ...
2322  0.34864163 0.50752205 0.8750529 \n 0.33083543 ...             padmasana
2323  0.21110085 0.5085427  0.9112413 \n 0.17171407 ...             padmasana
2324  0.35236198 0.48096877 0.84798944\n 0.32579598 ...             padmasana
2325  0.20688812 0.4861064  0.7983722 \n 0.1713758  ...             padmasana
2326  0.26876318 0.47743836 0.8376727 \n 0.22908282 ...             padmasana

[2327 rows x 2 columns]

In [ ]:
X = dataset_df["Keypoints"]


In [ ]:
classes = dataset_df["Class"]

In [ ]:
classes

0       adho mukha svanasana
1       adho mukha svanasana
2       adho mukha svanasana
3       adho mukha svanasana
4       adho mukha svanasana
                ...         
2322               padmasana
2323               padmasana
2324               padmasana
2325               padmasana
2326               padmasana
Name: Class, Length: 2327, dtype: object

In [ ]:
keypoints_arr = []
for i in range(X.shape[0]):
  keypoints=[]
  print("Before: ", X[i])
  datapoint =[float(value) for value in X[i].strip().split()]
  print("After: ", datapoint)
  for j in range(0,len(datapoint),3):
    keypoint = datapoint[j:j+3]
    print("Keypoint: ", keypoint)
    keypoints.append(keypoint)
  keypoints_arr.append(keypoints)

Streaming output truncated to the last 5000 lines.
 0.44455996 0.27446023 0.71305   
 0.46267682 0.2808074  0.7172639 
 0.5615702  0.5080646  0.36477932
 0.61396194 0.51351154 0.6309242 
 0.484937   0.70114404 0.24980925
 0.49327403 0.6925331  0.53776574
 0.5198004  0.6656401  0.50380194
 0.5556689  0.65308434 0.48442248
 0.5445158  0.870504   0.08397161
 0.5320988  0.9789094  0.41518256
 0.50690705 0.7834603  0.3239421 
 0.5139998  0.80559295 0.21064271
After:  [0.47955617, 0.05263289, 0.6475252, 0.50151324, 0.06681595, 0.6116885, 0.5003029, 0.06705988, 0.62407875, 0.51814115, 0.15282331, 0.5689675, 0.51785845, 0.15518402, 0.6715322, 0.44455996, 0.27446023, 0.71305, 0.46267682, 0.2808074, 0.7172639, 0.5615702, 0.5080646, 0.36477932, 0.61396194, 0.51351154, 0.6309242, 0.484937, 0.70114404, 0.24980925, 0.49327403, 0.6925331, 0.53776574, 0.5198004, 0.6656401, 0.50380194, 0.5556689, 0.65308434, 0.48442248, 0.5445158, 0.870504, 0.08397161, 0.5320988, 0.9789094, 0.41518256, 0.50690705, 0.78

In [ ]:
keypoints_arr

[[[0.6441565, 0.4670998, 0.74062914],
  [0.65457326, 0.44342688, 0.60968435],
  [0.6527129, 0.4425789, 0.61767256],
  [0.6248396, 0.40990397, 0.69232136],
  [0.62165016, 0.40593413, 0.6220944],
  [0.55732405, 0.42880335, 0.7678733],
  [0.548376, 0.4307836, 0.71603817],
  [0.67565304, 0.3407123, 0.87162846],
  [0.6482144, 0.3404241, 0.71263146],
  [0.7510547, 0.22129714, 0.79935944],
  [0.713113, 0.22960192, 0.82714826],
  [0.31796327, 0.6591909, 0.8140527],
  [0.31569543, 0.6526918, 0.5581159],
  [0.5300152, 0.7934507, 0.83366513],
  [0.5348201, 0.78051114, 0.7602109],
  [0.7162476, 0.9445977, 0.84313124],
  [0.706967, 0.9018351, 0.678858]],
 [[0.5874929, 0.5530081, 0.36677733],
  [0.5912886, 0.57880914, 0.4875698],
  [0.5979637, 0.5423819, 0.6476953],
  [0.5441783, 0.61291885, 0.6553475],
  [0.5459598, 0.5070507, 0.58395815],
  [0.4533296, 0.6429482, 0.8307974],
  [0.47144455, 0.4220951, 0.5250737],
  [0.6371874, 0.698002, 0.75916594],
  [0.6836041, 0.4654918, 0.683881],
  [0.803254, 

In [ ]:
keypoints

[[0.26876318, 0.47743836, 0.8376727],
 [0.22908282, 0.5122186, 0.7913937],
 [0.22854875, 0.44699955, 0.8679372],
 [0.19719537, 0.5594169, 0.65338045],
 [0.19431254, 0.40612316, 0.78891414],
 [0.35349005, 0.6450945, 0.7783009],
 [0.3426325, 0.32614264, 0.96400446],
 [0.63083595, 0.7417978, 0.8911636],
 [0.6141181, 0.22293757, 0.73516554],
 [0.5673381, 0.5108866, 0.7661726],
 [0.5646435, 0.44246662, 0.7666699],
 [0.7171934, 0.5846874, 0.91808295],
 [0.7060476, 0.3961391, 0.9002084],
 [0.880619, 0.78774035, 0.8188604],
 [0.93051475, 0.20823617, 0.88473535],
 [0.78098077, 0.4338888, 0.80734783],
 [0.8508136, 0.54773074, 0.60603327]]

In [ ]:
# Create a CSV file and write the header
csv_file_path = f"{MOUNT_PATH}/classes/keypoint_dataset_new.csv"  # Replace with the desired path for the CSV file
with open(csv_file_path, mode='w', newline='') as csv_file:
    csv_writer = csv.writer(csv_file)
    csv_writer.writerow(['k1_x', 'k1_y', 'k1_p', 'k2_x', 'k2_y', 'k2_p', 'k3_x', 'k3_y', 'k3_p', 'k4_x', 'k4_y', 'k4_p', 'k5_x', 'k5_y', 'k5_p', 'k6_x', 'k6_y', 'k6_p', 'k7_x', 'k7_y', 'k7_p', 'k8_x', 'k8_y', 'k8_p', 'k9_x', 'k9_y', 'k9_p', 'k10_x', 'k10_y', 'k10_p', 'k11_x', 'k11_y', 'k11_p', 'k12_x', 'k12_y', 'k12_p', 'k13_x', 'k13_y', 'k13_p', 'k14_x', 'k14_y', 'k14_p', 'k15_x', 'k15_y', 'k15_p', 'k16_x', 'k16_y', 'k16_p', 'k17_x', 'k17_y', 'k17_p', 'Class'])

    # Write each row (image path and label) to the CSV file
    # for keypoints, class_ in zip(keypoints_arr, classes):
    #     csv_writer.writerow([keypoints, class_])
    for i in range(X.shape[0]):
      print("Before: ", X[i])
      datapoint =[float(value) for value in X[i].strip().split()]
      print("After: ", datapoint)
      datapoint.append(classes[i])
      print("new datapoint: ", datapoint)
      csv_writer.writerow(datapoint)

Streaming output truncated to the last 5000 lines.
 0.5233991  0.05171156 0.7180108 
 0.52775794 0.04821855 0.69579506
After:  [0.522851, 0.90648365, 0.5331489, 0.5005279, 0.9170358, 0.5475041, 0.49703062, 0.91893935, 0.62136704, 0.45777494, 0.88663584, 0.52396554, 0.45737398, 0.8825126, 0.8588484, 0.44604656, 0.7995046, 0.7716064, 0.45384458, 0.796577, 0.62842697, 0.4620931, 0.6337541, 0.502456, 0.47003222, 0.6315089, 0.6021129, 0.5860396, 0.6421512, 0.62138873, 0.6082197, 0.64893806, 0.6674796, 0.43923634, 0.512004, 0.8180418, 0.44462165, 0.5112575, 0.70808315, 0.48054475, 0.28687257, 0.53215384, 0.48748964, 0.27617785, 0.5968707, 0.5233991, 0.05171156, 0.7180108, 0.52775794, 0.04821855, 0.69579506]
new datapoint:  [0.522851, 0.90648365, 0.5331489, 0.5005279, 0.9170358, 0.5475041, 0.49703062, 0.91893935, 0.62136704, 0.45777494, 0.88663584, 0.52396554, 0.45737398, 0.8825126, 0.8588484, 0.44604656, 0.7995046, 0.7716064, 0.45384458, 0.796577, 0.62842697, 0.4620931, 0.6337541, 0.502456, 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Streaming output truncated to the last 5000 lines.
 0.59922904 0.84452176 0.62463593
After:  [0.5658351, 0.13698342, 0.7440351, 0.5285675, 0.1164199, 0.7857058, 0.53124785, 0.11574041, 0.704729, 0.44424972, 0.16575776, 0.7116362, 0.4419589, 0.1636938, 0.6235945, 0.36629623, 0.35306856, 0.5091875, 0.41685542, 0.33956125, 0.38703662, 0.5210462, 0.63255686, 0.53657687, 0.5225295, 0.6257922, 0.5158014, 0.7737255, 0.6155589, 0.632946, 0.73974144, 0.6226185, 0.37938082, 0.2965304, 0.8013683, 0.60231996, 0.31644467, 0.7979718, 0.5701726, 0.64069504, 0.5416811, 0.11355153, 0.6265265, 0.47141254, 0.38015577, 0.60264903, 0.85534775, 0.4594171, 0.59922904, 0.84452176, 0.62463593]
new datapoint:  [0.5658351, 0.13698342, 0.7440351, 0.5285675, 0.1164199, 0.7857058, 0.53124785, 0.11574041, 0.704729, 0.44424972, 0.16575776, 0.7116362, 0.4419589, 0.1636938, 0.6235945, 0.36629623, 0.35306856, 0.5091875, 0.41685542, 0.33956125, 0.38703662, 0.5210462, 0.63255686, 0.53657687, 0.5225295, 0.6257922, 0.515801

In [ ]:
keypoints_arr = []
for i in range(X.shape[0]):
  keypoints=[]
  print("Before: ", X[i])
  datapoint =[float(value) for value in X[i].strip().split()]
  print("After: ", datapoint)
  for j in range(0,len(datapoint),3):
    keypoint = datapoint[j:j+3]
    print("Keypoint: ", keypoint)
    keypoints.append(keypoint)
  keypoints_arr.append(keypoints)

Streaming output truncated to the last 5000 lines.
Keypoint:  [0.26675367, 0.42427352, 0.45328194]
Keypoint:  [0.09817521, 0.5244777, 0.44565234]
Keypoint:  [0.24857467, 0.5292295, 0.32060984]
Keypoint:  [0.55198973, 0.5586135, 0.72094303]
Keypoint:  [0.5475728, 0.422833, 0.8393738]
Keypoint:  [0.7721817, 0.48295248, 0.63042045]
Keypoint:  [0.7217779, 0.5702682, 0.74489194]
Keypoint:  [0.9686067, 0.471412, 0.8022748]
Keypoint:  [0.8510718, 0.4729817, 0.50201255]
Before:  0.11898031 0.52096874 0.4685259 
 0.10085559 0.5430358  0.6733035 
 0.1018092  0.49623564 0.63484555
 0.1297595  0.5666669  0.79085106
 0.12606186 0.46743065 0.7043643 
 0.24421135 0.6168249  0.6760427 
 0.25756004 0.38871685 0.8794098 
 0.33282274 0.53279316 0.18984957
 0.33675835 0.5276295  0.57439554
 0.17218067 0.53316283 0.32522374
 0.15263434 0.5407966  0.44674587
 0.5565864  0.56486624 0.7466627 
 0.5502979  0.43766356 0.64255184
 0.80938876 0.50159323 0.7849244 
 0.76247615 0.6191877  0.69076586
 0.9708775  0.4

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



 [0.75755125, 0.47528544, 0.91750604]
Keypoint:  [0.16957292, 0.44342825, 0.70440626]
Keypoint:  [0.96243215, 0.483761, 0.8077665]
Before:  0.2678208  0.3662271  0.83683664
 0.24701568 0.3820179  0.8940738 
 0.24822965 0.3630733  0.7755169 
 0.2484365  0.44260317 0.86039287
 0.25126302 0.39757663 0.6181304 
 0.2794292  0.53149104 0.88130295
 0.37260264 0.39911798 0.51436687
 0.24611703 0.622443   0.5994768 
 0.38513476 0.2626353  0.7448528 
 0.19481084 0.7447605  0.82006854
 0.3593858  0.13679753 0.53803676
 0.41780576 0.70182705 0.6572476 
 0.49115503 0.66143924 0.7692057 
 0.36584136 0.8986519  0.7492584 
 0.6941319  0.6587612  0.85004365
 0.19812788 0.75872195 0.6866745 
 0.92944825 0.6496511  0.91670394
After:  [0.2678208, 0.3662271, 0.83683664, 0.24701568, 0.3820179, 0.8940738, 0.24822965, 0.3630733, 0.7755169, 0.2484365, 0.44260317, 0.86039287, 0.25126302, 0.39757663, 0.6181304, 0.2794292, 0.53149104, 0.88130295, 0.37260264, 0.39911798, 0.51436687, 0.24611703, 0.622443, 0.5994768